In [3]:
#import required packages
import random
random.seed(42)
from glob import glob
from collections import defaultdict

import numpy as np
from numpy.random import choice

from symusic import Score
from miditok import REMI, TokenizerConfig
from midiutil import MIDIFile

from datasets import load_dataset

In [9]:
import pretty_midi
from IPython.display import Audio

In [4]:
# get our pokemon diamond midi files
midi_files = glob('./midi_dataset/*.mid')
#midi_files = glob('./drive/MyDrive/midi-classical-music/data/*.mid')
len(midi_files)

100

In [10]:
midi_data = pretty_midi.PrettyMIDI(midi_files[0])
audio = midi_data.synthesize(fs=22050)
Audio(audio, rate=22050)

In [87]:
from music21 import converter, stream, meter
def split_score(score, bars_per_split=16):
    # Get initial time signature
    ts = score.recurse().getElementsByClass(meter.TimeSignature)
    beats_per_bar, beat_type = (4, 4)
    if ts:
        beats_per_bar = ts[0].numerator
        beat_type = ts[0].denominator

    bar_duration = beats_per_bar * (4 / beat_type)
    total_duration = score.highestTime
    split_duration = bars_per_split * bar_duration
    num_splits = int(total_duration // split_duration) + 1

    flattened_parts = [part.flat.notesAndRests for part in score.parts]

    # Pre-filtered metadata
    key_sigs = [el for el in score.flat.getElementsByClass('KeySignature')]
    time_sigs = [el for el in score.flat.getElementsByClass(meter.TimeSignature)]

    chunks = []

    for i in range(num_splits):
        start_time = i * split_duration
        end_time = start_time + split_duration
        chunk_score = stream.Score()

        # Add relevant global metadata
        for ks in key_sigs:
            if ks.offset <= start_time:
                chunk_score.insert(0, ks)
        for ts in time_sigs:
            if ts.offset <= start_time:
                chunk_score.insert(0, ts)

        # Process each part
        for part_stream in flattened_parts:
            new_part = stream.Part()
            # Insert elements directly without calling .clone()
            for el in part_stream.getElementsByOffset(start_time, end_time):
                new_part.insert(el.offset - start_time, el) # Changed line
            chunk_score.append(new_part)

        has_notes = False
        for el in chunk_score.flat.notesAndRests:
            if el.offset <= end_time:
                has_notes = True
                break

        # filter out anything less than 2 bars
        if has_notes and (end_time - start_time) >= 2 * bar_duration:
            chunks.append(chunk_score)

    return chunks

In [86]:
from tqdm import tqdm
for file_path in tqdm(midi_files, desc="Processing MIDI files"):
  score = converter.parse(file_path)
  chunks = split_score(score, bars_per_split=8) # for pokemon music, splitting to 8 bars because of its loopiness
  for i, chunk in enumerate(chunks):
    filename = file_path.split("/")[-1].split(".")[0].split("\\")[1]
    output_path = "./midi_chunks/" + filename + "_part_" + str(i + 1) + ".mid"
    chunk.write("midi", fp=output_path)

Processing MIDI files:   0%|          | 0/100 [00:01<?, ?it/s]


StreamException: cannot process repeats on Stream that does not contain measures

In [38]:
from miditok import REMI, TokenizerConfig
from pathlib import Path
import json


# Use REMIPlus tokenizer with appropriate config
config = TokenizerConfig()
config.use_programs = True
config.one_token_stream_for_programs = True
config.use_time_signatures = True

tokenizer = REMI(config)

midi_dir = Path("./midi_chunks")
token_dir = Path("./remi_tokens")
token_dir.mkdir(exist_ok=True)

# Tokenize all MIDI files
for midi_path in midi_dir.glob("*.mid"):
    tokens = tokenizer(midi_path)  # REMIPlus will return a single TokenSequence

    print(f"{midi_path.name}: {len(tokens.ids)} tokens")

    # Save tokens to JSON
    with open(token_dir / (midi_path.stem + ".json"), "w") as f:
        json.dump({"ids": tokens.ids}, f)

c:\Users\Admin\Documents\153\.venv\Lib\site-packages\miditok\tokenizations\remi.py:88: UserWarning: Attribute controls are not compatible with 'config.one_token_stream_for_programs' and multi-vocabulary tokenizers. Disabling them from the config.
  super().__init__(tokenizer_config, params)


A New Adventure!_part_1.mid: 1721 tokens
A New Adventure!_part_2.mid: 2737 tokens
A New Adventure!_part_3.mid: 1312 tokens
A New Adventure!_part_4.mid: 598 tokens
Amity Square_part_1.mid: 1641 tokens
Amity Square_part_2.mid: 2050 tokens
Amity Square_part_3.mid: 2938 tokens
Amity Square_part_4.mid: 1491 tokens
Battle Arcade_part_1.mid: 2491 tokens
Battle Arcade_part_2.mid: 2883 tokens
Battle Arcade_part_3.mid: 3123 tokens
Battle Arcade_part_4.mid: 3400 tokens
Battle Castle_part_1.mid: 1312 tokens
Battle Castle_part_2.mid: 2492 tokens
Battle Castle_part_3.mid: 2333 tokens
Battle Castle_part_4.mid: 2123 tokens
Battle Castle_part_5.mid: 70 tokens
Battle Factory_part_1.mid: 1741 tokens
Battle Factory_part_2.mid: 2344 tokens
Battle Factory_part_3.mid: 2049 tokens
Battle Factory_part_4.mid: 1925 tokens
Battle Factory_part_5.mid: 46 tokens
Battle Hall_part_1.mid: 1577 tokens
Battle Hall_part_2.mid: 2161 tokens
Battle Hall_part_3.mid: 1960 tokens
Battle Hall_part_4.mid: 2480 tokens
Battle Hall_

In [92]:
import torch

# Use GPU if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

Using device: cuda


In [109]:
import torch.nn as nn
class MusicTransformer(nn.Module):
    def __init__(self, vocab_size, d_model=512, nhead=8, num_layers=6, max_len=2048):
        super().__init__()
        self.embedding = nn.Embedding(vocab_size, d_model)
        self.pos_encoding = nn.Parameter(torch.zeros(1, max_len, d_model))  # learnable pos encoding
        encoder_layer = nn.TransformerEncoderLayer(d_model, nhead)
        self.transformer = nn.TransformerEncoder(encoder_layer, num_layers)
        self.fc_out = nn.Linear(d_model, vocab_size)

    def forward(self, x):
        x = self.embedding(x) + self.pos_encoding[:, :x.size(1), :]
        x = self.transformer(x)
        return self.fc_out(x)

In [110]:
from torch.utils.data import Dataset, DataLoader
from pathlib import Path

class MIDITokenDataset(Dataset):
    def __init__(self, token_dir, max_seq_len=2048):
        self.token_paths = list(Path(token_dir).glob("*.json"))
        self.max_seq_len = max_seq_len

    def __len__(self):
        return len(self.token_paths)

    def __getitem__(self, idx):
        with open(self.token_paths[idx], "r") as f:
            tokens = json.load(f)["ids"]
        tokens = tokens[:self.max_seq_len]
        input_ids = torch.tensor(tokens[:-1], dtype=torch.long)
        target_ids = torch.tensor(tokens[1:], dtype=torch.long)
        return input_ids, target_ids

In [111]:
from torch.nn.utils.rnn import pad_sequence

def collate_fn(batch):
    input_ids, target_ids = zip(*batch)
    input_ids = pad_sequence(input_ids, batch_first=True, padding_value=0)
    target_ids = pad_sequence(target_ids, batch_first=True, padding_value=0)
    return input_ids, target_ids


In [112]:
vocab_size = len(tokenizer.vocab)

model = MusicTransformer(vocab_size).to(device)
optimizer = torch.optim.Adam(model.parameters(), lr=1e-4)
criterion = nn.CrossEntropyLoss()

# Data
dataset = MIDITokenDataset("./remi_tokens", max_seq_len=2048)
dataloader = DataLoader(dataset, batch_size=8, shuffle=True, collate_fn=collate_fn)

# Train
for epoch in range(10):
    model.train()
    total_loss = 0

    for batch in dataloader:
        input_ids, target_ids = batch
        input_ids = input_ids.to(device)
        target_ids = target_ids.to(device)

        optimizer.zero_grad()
        output = model(input_ids)

        # output: [B, T, vocab], target_ids: [B, T] → flatten for CrossEntropyLoss
        loss = criterion(output.view(-1, vocab_size), target_ids.view(-1))
        loss.backward()
        optimizer.step()

        total_loss += loss.item()

    print(f"Epoch {epoch+1}, Loss: {total_loss / len(dataloader):.4f}")

c:\Users\Admin\Documents\153\.venv\Lib\site-packages\torch\nn\modules\transformer.py:382: UserWarning: enable_nested_tensor is True, but self.use_nested_tensor is False because encoder_layer.self_attn.batch_first was not True(use batch_first for better inference performance)
  warnings.warn(


Epoch 1, Loss: 2.3208
Epoch 2, Loss: 1.5934
Epoch 3, Loss: 1.5344
Epoch 4, Loss: 1.5130
Epoch 5, Loss: 1.5172
Epoch 6, Loss: 1.4912
Epoch 7, Loss: 1.4869
Epoch 8, Loss: 1.4875
Epoch 9, Loss: 1.4858
Epoch 10, Loss: 1.4915


In [115]:
from miditok import TokSequence
from collections import Counter
import torch.nn.functional as F
model.eval()
vocab = tokenizer.vocab
inverse_vocab = {v: k for k, v in vocab.items()}
with torch.no_grad():
    seed_tokens = [tokenizer.vocab['Bar_None']] + \
              [tokenizer.vocab[f'Position_{i}'] for i in range(32)]
    seed = torch.tensor([seed_tokens], dtype=torch.long).to(device)
    generated = seed

    for _ in range(1024):
        output = model(generated)
        temperature = 1.0  # tweak: 0.7 - 1.0 usually works well
        top_k = 50  # restrict to top 50 candidates

        logits = output[:, -1, :] / temperature
        topk_logits, topk_indices = torch.topk(logits, top_k)

        probs = F.softmax(topk_logits, dim=-1)
        next_token = topk_indices.gather(-1, torch.multinomial(probs, 1))
        generated = torch.cat((generated, next_token), dim=1)
    sequence = TokSequence(ids=generated.squeeze().tolist())
    print(len(sequence))
    print("Sample tokens as strings:", [inverse_vocab[id] for id in sequence[:50]])
    token_strings = [inverse_vocab[id] for id in sequence]
    print(Counter(token_strings).most_common(20))
    midi = tokenizer.decode(sequence)
    midi.dump_midi("test_generated.mid")

1057
Sample tokens as strings: ['Bar_None', 'Position_0', 'Position_1', 'Position_2', 'Position_3', 'Position_4', 'Position_5', 'Position_6', 'Position_7', 'Position_8', 'Position_9', 'Position_10', 'Position_11', 'Position_12', 'Position_13', 'Position_14', 'Position_15', 'Position_16', 'Position_17', 'Position_18', 'Position_19', 'Position_20', 'Position_21', 'Position_22', 'Position_23', 'Position_24', 'Position_25', 'Position_26', 'Position_27', 'Position_28', 'Position_29', 'Position_30', 'Position_31', 'Program_0', 'Pitch_53', 'Velocity_111', 'Duration_1.0.8', 'Position_20', 'Program_0', 'Pitch_62', 'Velocity_111', 'Duration_0.4.8', 'Program_0', 'Pitch_40', 'Velocity_111', 'Duration_0.2.8', 'Program_0', 'Pitch_72', 'Velocity_83', 'Duration_0.2.8']
[('Program_0', 238), ('Velocity_111', 131), ('Duration_0.2.8', 95), ('Duration_0.4.8', 56), ('Velocity_127', 35), ('Duration_0.3.8', 31), ('Duration_1.0.8', 23), ('Velocity_39', 11), ('Pitch_42', 10), ('Duration_1.4.8', 10), ('Pitch_36'

In [116]:
midi_data = pretty_midi.PrettyMIDI("test_generated.mid")
audio = midi_data.synthesize(fs=22050)
Audio(audio, rate=22050)

In [80]:
test_data = pretty_midi.PrettyMIDI("midi_chunks/A New Adventure!_part_1.mid")
audio = test_data.synthesize(fs=22050)
Audio(audio, rate=22050)

In [105]:
with open("remi_tokens/A New Adventure!_part_2.json", "r") as f:
    tokens = json.load(f)["ids"]

    token_strings = [inverse_vocab[id] for id in tokens]
    print(token_strings[:50])
    token_counter = Counter(token_strings)
    for t in token_counter:
        if t.startswith("Bar") or t.startswith("Position"):
            print(f"{t}: {token_counter[t]}")
midi = tokenizer.decode(TokSequence(ids=tokens))
midi.dump_midi("test_reconstructed.mid")
midi_data = pretty_midi.PrettyMIDI("test_reconstructed.mid")
audio = midi_data.synthesize(fs=22050)
Audio(audio, rate=22050)

['Bar_None', 'TimeSig_4/4', 'Position_0', 'Program_0', 'Pitch_54', 'Velocity_111', 'Duration_0.3.8', 'Program_0', 'Pitch_57', 'Velocity_111', 'Duration_0.3.8', 'Program_0', 'Pitch_57', 'Velocity_111', 'Duration_0.3.8', 'Program_0', 'Pitch_62', 'Velocity_111', 'Duration_0.3.8', 'Program_0', 'Pitch_62', 'Velocity_111', 'Duration_0.7.8', 'Program_0', 'Pitch_45', 'Velocity_127', 'Duration_1.0.8', 'Program_0', 'Pitch_74', 'Velocity_111', 'Duration_1.3.8', 'Program_0', 'Pitch_74', 'Velocity_111', 'Duration_1.4.8', 'Position_3', 'Program_0', 'Pitch_54', 'Velocity_111', 'Duration_0.3.8', 'Program_0', 'Pitch_57', 'Velocity_111', 'Duration_0.3.8', 'Program_0', 'Pitch_59', 'Velocity_111', 'Duration_0.3.8', 'Program_0', 'Pitch_66']
Bar_None: 9
Position_0: 9
Position_3: 8
Position_5: 8
Position_6: 8
Position_8: 8
Position_10: 3
Position_11: 8
Position_12: 3
Position_13: 8
Position_16: 8
Position_19: 8
Position_21: 8
Position_22: 7
Position_24: 8
Position_26: 8
Position_27: 8
Position_28: 8
Position

In [104]:
testtoks = tokenizer("./midi_dataset/A New Adventure!.mid")
print(testtoks)
token_counter = Counter(testtoks.tokens)
for t in token_counter:
    if t.startswith("Bar") or t.startswith("Position"):
        print(f"{t}: {token_counter[t]}")

TokSequence(tokens=['Bar_None', 'TimeSig_4/4', 'Position_0', 'Program_48', 'Pitch_45', 'Velocity_111', 'Duration_0.3.8', 'Program_48', 'Pitch_64', 'Velocity_111', 'Duration_0.3.8', 'Position_3', 'Program_48', 'Pitch_52', 'Velocity_111', 'Duration_0.3.8', 'Program_48', 'Pitch_69', 'Velocity_111', 'Duration_0.3.8', 'Position_5', 'Program_48', 'Pitch_57', 'Velocity_111', 'Duration_0.3.8', 'Program_48', 'Pitch_71', 'Velocity_111', 'Duration_0.3.8', 'Position_8', 'Program_48', 'Pitch_59', 'Velocity_111', 'Duration_0.3.8', 'Program_48', 'Pitch_64', 'Velocity_111', 'Duration_0.3.8', 'Position_11', 'Program_48', 'Pitch_57', 'Velocity_111', 'Duration_0.3.8', 'Program_48', 'Pitch_69', 'Velocity_111', 'Duration_0.3.8', 'Position_13', 'Program_48', 'Pitch_59', 'Velocity_111', 'Duration_0.3.8', 'Program_48', 'Pitch_71', 'Velocity_111', 'Duration_0.3.8', 'Position_16', 'Program_48', 'Pitch_64', 'Velocity_111', 'Duration_0.3.8', 'Program_48', 'Pitch_64', 'Velocity_111', 'Duration_0.3.8', 'Position_19